In [ ]:
from pathlib import Path
import SimpleITK as sitk

# Create a directory to store converted nii.gz files
nii_results_path = Path("./nii_results")
nii_results_path.mkdir(parents = True, exist_ok = True)

# Create a directory to store elastix results 
elastix_results_path = Path("./elastix_results")
elastix_results_path.mkdir(parents = True, exist_ok = True)

# Create a directory to store transformix results
transformix_results_path = Path("./transformix_results")    
transformix_results_path.mkdir(parents = True, exist_ok = True)

In [3]:
# Convert brain MRI mgz to nii.gz
freesurfer_path = Path("./MSLesSeg After FreeSurfer")
missing_file = Path("./nii_results/missing_files.txt") # Log missing brain.mgz files

if missing_file.exists():
    missing_file.unlink()
for sub_dir in freesurfer_path.iterdir():
    if sub_dir.is_dir():
        brain_path = sub_dir / "mri" / "brain.mgz"
        if brain_path.exists():
            converted_brain_path = nii_results_path / f"{sub_dir.name}_brain.nii.gz"
            sitk.WriteImage(sitk.ReadImage(str(brain_path)), str(converted_brain_path))
        else:
            with open(missing_file, "a", encoding = "utf-8") as f:
                f.write(f"{sub_dir.name} has no brain.mgz\n")

In [ ]:
# Arrange converted brain nii.gz files in a dictionnary associated with their split name
brain_split_path_dict = {} # this dictionnary takes split path list as key and path as value

for nii_file in nii_results_path.rglob("*.nii.gz"):
    arg = nii_file.name.split("_")
    arg[-1] = arg[-1].split(".")
    arg = tuple(arg[:-1] + arg[-1])
    brain_split_path_dict[arg] = nii_file
    # print(arg)
    
print(brain_split_path_dict)

{('P10', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P10_T1_T1_brain.nii.gz'), ('P10', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P10_T2_T1_brain.nii.gz'), ('P11', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P11_T1_T1_brain.nii.gz'), ('P11', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P11_T2_T1_brain.nii.gz'), ('P12', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P12_T1_T1_brain.nii.gz'), ('P12', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P12_T2_T1_brain.nii.gz'), ('P12', 'T3', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P12_T3_T1_brain.nii.gz'), ('P13', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P13_T1_T1_brain.nii.gz'), ('P13', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P13_T2_T1_brain.nii.gz'), ('P14', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P14_T1_T1_brain.nii.gz'), ('P14', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii

In [ ]:
# Arrange T1 dataset nii.gz files in a dictionnary associated with their split name
mslesseg_path = Path("./MSLesSeg Dataset")
t1_split_path_dict = {}

for split_dir in ["train", "test"]:
    split_path = mslesseg_path / split_dir
    
    if not split_path.exists():
        continue
    
    for t1_path in split_path.rglob("*.nii.gz"):
        if t1_path.name.endswith("_T1.nii.gz"):
            # print(t1_path)
            arg = t1_path.name.split("_")
            if len(arg) == 2:
                arg.insert(1, "T1")
            
            arg[-1] = arg[-1].split(".")
            arg = tuple(arg[:-1] + arg[-1])
            t1_split_path_dict[arg] = t1_path
            # print(arg)

print(t1_split_path_dict)


{('P1', 'T1', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P1/T1/P1_T1_T1.nii.gz'), ('P1', 'T2', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P1/T2/P1_T2_T1.nii.gz'), ('P1', 'T3', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P1/T3/P1_T3_T1.nii.gz'), ('P10', 'T1', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P10/T1/P10_T1_T1.nii.gz'), ('P10', 'T2', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P10/T2/P10_T2_T1.nii.gz'), ('P11', 'T1', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P11/T1/P11_T1_T1.nii.gz'), ('P11', 'T2', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P11/T2/P11_T2_T1.nii.gz'), ('P12', 'T1', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P12/T1/P12_T1_T1.nii.gz'), ('P12', 'T2', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P12/T2/P12_T2_T1.nii.gz'), ('P12', 'T3', 'T1', 'nii', 'gz'): WindowsPath('MSLesSeg Dataset/train/P12/T3/P12_T3_T1.nii.gz'), ('P12', 'T4', 'T1', 'nii', 'gz'): Wind

In [ ]:
# Arrange valid brain nii.gz files that have their corresponding T1 nii.gz files in the dataset
from copy import deepcopy

valid_brain_split_path_dict = deepcopy(brain_split_path_dict)
missing_file2 = Path("./elastix_results/missing_files.txt")²

if missing_file2.exists():
    missing_file2.unlink()
    
extracted_t1_split = [split[0:2] for split in t1_split_path_dict.keys()] # split[0:2] is (patient_id, timepoint_id)

for split in brain_split_path_dict.keys():
    if split[0:2] not in extracted_t1_split:
        with open(missing_file2, "a", encoding = "utf-8") as f:
            f.write(f"{('_'.join(split)) + '_T1'} exists in FreeSurfer but not in the dataset\n")
        # print(brain + ("T1", "brain", "nii", "gz"))
        valid_brain_split_path_dict.pop((split[0:2] + ("T1", "brain", "nii", "gz")), None) # remove invalid brains
        
print(valid_brain_split_path_dict)
print(("P17", "T2", "T1", "brain", "nii", "gz") in valid_brain_split_path_dict.keys()) # not valid because P17_T2_T1.nii.gz does not exist in dataset
print(("P12","T4", "T1", "brain", "nii", "gz") in valid_brain_split_path_dict.keys()) # not valid because brain.mgz of P12_T4_T1 does not exist in FreeSurfer data
print(("P5", "T2", "T1", "brain", "nii", "gz") in valid_brain_split_path_dict.keys())

{('P10', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P10_T1_T1_brain.nii.gz'), ('P10', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P10_T2_T1_brain.nii.gz'), ('P11', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P11_T1_T1_brain.nii.gz'), ('P11', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P11_T2_T1_brain.nii.gz'), ('P12', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P12_T1_T1_brain.nii.gz'), ('P12', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P12_T2_T1_brain.nii.gz'), ('P12', 'T3', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P12_T3_T1_brain.nii.gz'), ('P13', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P13_T1_T1_brain.nii.gz'), ('P13', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P13_T2_T1_brain.nii.gz'), ('P14', 'T1', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii_results/P14_T1_T1_brain.nii.gz'), ('P14', 'T2', 'T1', 'brain', 'nii', 'gz'): WindowsPath('nii

' associate brain_pasts_list with brain_split_list , idem for t1'

In [ ]:
# Elastix registration
import subprocess

t1_map = {split[0:2]: path for split, path in t1_split_path_dict.items()}

for split, brain_path in valid_brain_split_path_dict.items():
        extracted_split = split[0:2]
        t1_path = t1_map.get(extracted_split, None)
        
        if t1_path is not None:
            dir_path = elastix_results_path / f"{'_'.join(extracted_split)}"
            dir_path.mkdir(parents = True, exist_ok = True)
            cmd = [
            "elastix",
            "-m", str(brain_path),
            "-f", str(t1_path),
            "-p", "Parameters.T1Brain.affine.txt",
            "-out", str(dir_path)
            ]
            result = subprocess.run(cmd, capture_output = True, text = True, shell = True)
            print(f"Running {' '.join(cmd)}")
            print(result.stdout)
            print(result.stderr)

Running: elastix -m nii_results\P10_T1_T1_brain.nii.gz -f MSLesSeg Dataset\train\P10\T1\P10_T1_T1.nii.gz -p Parameters.T1Brain.affine.txt -out elastix_results\P10_T1
STDOUT: 
elastix is started at Sun Dec 14 18:18:50 2025.

which elastix:   elastix
  elastix version: 5.2.0
  Git revision SHA: ebb429a33bdf3248c2137fc4adb4259a2ec7db24
  Git revision date: Thu Jul 18 14:42:31 2024 +0200
  Build date: Jul 18 2024 13:02:32
  Compiler: Visual C++ version 194033812.0
  Memory address size: 64-bit
  CMake version: 3.24.2
  ITK version: 5.4.0

Command-line arguments: 
  -m nii_results\P10_T1_T1_brain.nii.gz -f "MSLesSeg Dataset\train\P10\T1\P10_T1_T1.nii.gz" -p Parameters.T1Brain.affine.txt -out elastix_results\P10_T1

elastix runs at: LAPTOP-QLNT3LMN
  Windows  Personal (x64),  (Build 9200)
  with 15774 MB memory, and 8 cores @ 3293 MHz.
-------------------------------------------------------------------------

Running elastix with parameter file 0: "Parameters.T1Brain.affine.txt".

Current ti

KeyboardInterrupt: 